In [1]:
import torch
from pyqcu.ascend import dslash
from pyqcu.ascend import inverse
dof = 4
latt_size = (16, 16, 16, 16)
# latt_size = (4, 8, 8, 8)
# latt_size = (8, 8, 8, 4)
# latt_size = (16, 8, 8, 8)
# latt_size = (8, 8, 8, 8)
# latt_size = (4, 4, 4, 4)
kappa = 0.125
# dtype = torch.complex128
dtype = torch.complex64
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f"Using device: {device}")
# Initialize lattice gauge theory
wilson = dslash.wilson_parity(
    latt_size=latt_size,
    kappa=kappa,
    dtype=dtype,
    device=device,
    verbose=False
)
clover = dslash.clover_parity(
    latt_size=latt_size,
    kappa=kappa,
    dtype=dtype,
    device=device,
    verbose=False
)
U = wilson.generate_gauge_field(sigma=0.1, seed=42)
null_vecs = torch.randn(dof, 4, 3, latt_size[3], latt_size[2], latt_size[1], latt_size[0],
                        dtype=dtype, device=device)
clover_term = clover.make_clover(U=U)
clover_term = clover.add_I(clover=clover_term)  # needed!


b = torch.randn_like(null_vecs[0])
U_eo = dslash.xxxtzyx2pxxxtzyx(input_array=U)
clover_eo = dslash.xxxtzyx2pxxxtzyx(input_array=clover_term)


    @@@@@@######QCU NOTES START######@@@@@@@
    Guide:
    0. Required: MPI(e.g. 4.1.2), CUDA(e.g. 12.4), CMAKE(e.g. 3.22.1), GCC(e.g. 11.4.0), HDF5-MPI(e.g. 1.10.7,'apt install libhdf5-mpi-dev && export HDF5_MPI="ON" && pip install --no-binary=h5py h5py').
    1. The libqcu.so was compiled when pyqcu setup in download_path/PyQCU/lib, please add this path to your LD_LIBRARY_PATH.
    2. The QCU(PyQCU) splite grid by x->y->z->t, lattice by x->y->z->t->p->d->c->c or x->y->z->t->c->s(->p) and x->y->z->t->c->s->c->s(->p).
    3. The QUDA(PyQUDA) splite grid by t->z->y->x, lattice by c->c->x->y->z->t->p->d or c->s->x->y->z->t(->p) and c->s->c->s->x->y->z->t(->p).
    4. The QCU input params in numpy array(dtype=np.int32), argv in  numpy array(dtype=np.float32 or float64) array, set_ptrs in numpy array(dtype=np.int64), other in cupy array(dtype=cp.complex64 or complex128).
    5. The smallest lattice size is (wilson:x=4,y=4,z=4,t=4;clover:x=8,y=8,z=8,t=8) that QCU support (when '#define _B

In [2]:
from pyqcu.ascend import inverse
mg = inverse.mg(b=b, wilson=wilson, U_eo=U_eo,
                clover=clover, clover_eo=clover_eo, dof=dof,verbose=True)

Building grid list:
  Level 0: 16x16x16x16
  Level 1: 8x8x8x8
  Level 2: 4x4x4x4
  Level 3: 2x2x2x2
self.grid_list:[[16, 16, 16, 16], [8, 8, 8, 8], [4, 4, 4, 4], [2, 2, 2, 2]]
BICGSTAB:Iteration 0: Residual = 1.682273e+02, Time = 0.038638 s
BICGSTAB:Iteration 1: Residual = 5.454161e+01, Time = 0.031883 s
BICGSTAB:Iteration 2: Residual = 1.056166e+02, Time = 0.029271 s
BICGSTAB:Iteration 3: Residual = 1.730878e+01, Time = 0.028748 s
BICGSTAB:Iteration 4: Residual = 1.550320e+01, Time = 0.029121 s
BICGSTAB:Iteration 5: Residual = 7.247091e+00, Time = 0.031943 s
BICGSTAB:Iteration 6: Residual = 5.021586e+00, Time = 0.030389 s
BICGSTAB:Iteration 7: Residual = 1.433360e+01, Time = 0.028612 s
BICGSTAB:Iteration 8: Residual = 5.673760e+00, Time = 0.028316 s
BICGSTAB:Iteration 9: Residual = 3.969816e+00, Time = 0.027938 s
BICGSTAB:Iteration 10: Residual = 4.672291e+00, Time = 0.027126 s
BICGSTAB:Iteration 11: Residual = 2.567762e+00, Time = 0.028776 s
BICGSTAB:Iteration 12: Residual = 2.099750

In [3]:
x=mg.solve()


MG:Iteration 1:
V-cycle level 0, mg_size: [16, 16, 16, 16]
    Pre pre-smooth residual norm: 9.9335e+02
    Pre-smoothing...
    Post pre-smooth residual norm: 3.4259e+01
restrict:shape,dof:(torch.Size([4, 4, 3, 8, 2, 8, 2, 8, 2, 8, 2]), 4)
EscTtZzYyXx,scTtZzYyXx->ETZYX
V-cycle level 1, mg_size: [8, 8, 8, 8]
    Pre pre-smooth residual norm: 1.1749e+01
    Pre-smoothing...
    Post pre-smooth residual norm: 1.6296e+00
restrict:shape,dof:(torch.Size([4, 4, 4, 2, 4, 2, 4, 2, 4, 2]), 4)
EeTtZzYyXx,eTtZzYyXx->ETZYX
V-cycle level 2, mg_size: [4, 4, 4, 4]
    Pre pre-smooth residual norm: 7.2331e-01
    Pre-smoothing...
    Post pre-smooth residual norm: 6.9237e-02
restrict:shape,dof:(torch.Size([4, 4, 2, 2, 2, 2, 2, 2, 2, 2]), 4)
EeTtZzYyXx,eTtZzYyXx->ETZYX
V-cycle level 3, mg_size: [2, 2, 2, 2]
    Pre-solve residual norm: 3.2591e-02
    Solving coarsest grid directly...
    Post-solve residual norm: 3.0436e-08
prolong:shape,dof:(torch.Size([4, 4, 2, 2, 2, 2, 2, 2, 2, 2]), 4)
EeTtZzYyXx, 

KeyboardInterrupt: 